I like looking at live data visualizations, like the World Air Quality Index ([WAQI](http://waqi.info/)). It puts together thousands of measuring station data feeds and shows them on a map. However, the main visualization is not really a mapping, but rather a map with markers. 
Is it possible to use the same data and generate an interactive map? This post is a write-down of my attempt.

If you're wondering what the Air Quality Index is, here is some more information (from [here](https://www.airnow.gov/index.cfm?action=aqibasics.aqi)):

> Think of the AQI as a yardstick that runs from 0 to 500. The higher the AQI value, the greater the level of air pollution and the greater the health concern. For example, an AQI value of 50 represents good air quality with little potential to affect public health, while an AQI value over 300 represents hazardous air quality.

If my understanding of [this calculator](https://www.airnow.gov/index.cfm?action=airnow.calculator) is correct, then the AQI is just a mapping, that depends on the considered pollutant, from concentration in the air to a number between 0 and 500. 

# The WAQI API 

To access the WAQI API, we need a token, which can be obtained by registering an account with them (see [here](https://aqicn.org/api/)).

Once we have this, we can use the API to fetch some data. Here's how it goes in Python. Most API calls start with the same base URL, so let's declare this first, as well as the loading of my personal token.

In [2]:
import requests

base_url = "https://api.waqi.info"

# read secret token from file containing the token as a single string
# you need to create this file if you want to reproduce this analysis
token = open('waqitoken.txt').read()

## City request 

We can do a basic city request with the following code (see <http://aqicn.org/json-api/doc/#api-City_Feed-GetCityFeed> for details) that prints the Air Quality Index (AQI) in the location that best matches the search string:

In [19]:
city = 'Roma'
r = requests.get(base_url + f"/feed/{city}/?token={token}")
"City: {}, Air quality index: {}".format(r.json()['data']['city']['name'], r.json()['data']['aqi'])

'City: Arenula, Roma, Lazio, Italy, Air quality index: 25'

In [20]:
r.json()['data']['iaqi']

{'h': {'v': 47.8},
 'no2': {'v': 6.4},
 'o3': {'v': 22.8},
 'p': {'v': 1021.2},
 'pm10': {'v': 16},
 'pm25': {'v': 25},
 't': {'v': 17},
 'w': {'v': 1.5},
 'wg': {'v': 6.1}}

In [21]:
r.json()['data']['time']

{'s': '2020-03-15 23:00:00', 'tz': '+01:00', 'v': 1584313200}

In [16]:
city = 'New York'
r = requests.get(base_url + f"/feed/{city}/?token={token}")
"City: {}, Air quality index: {}".format(r.json()['data']['city']['name'], r.json()['data']['aqi'])

'City: New York, Air quality index: 23'

In [4]:
city = 'Beijing'
r = requests.get(base_url + f"/feed/{city}/?token={token}")
"City: {}, Air quality index: {}".format(r.json()['data']['city']['name'], r.json()['data']['aqi'])

'City: Beijing (北京), Air quality index: 82'

In [5]:
city = 'Berlin'
r = requests.get(base_url + f"/feed/{city}/?token={token}")
"City: {}, Air quality index: {}".format(r.json()['data']['city']['name'], r.json()['data']['aqi'])

'City: Berlin, Germany, Air quality index: 68'

## Searching by coordinates

The API also allows to search by latitude / longitude coordinates (see <http://aqicn.org/json-api/doc/#api-Geolocalized_Feed-GetGeolocFeed>):

In [6]:
lat, lng = 43.6604, 7.1531
r = requests.get(base_url + f"/feed/geo:{lat};{lng}/?token={token}")
"Station: {}, Air quality index: {}".format(r.json()['data']['city']['name'], r.json()['data']['aqi'])

'Station: Nice Aeroport, PACA, France, Air quality index: 35'

## Map query 

Since our goal is to make a map, the most useful API query is the one allowing to define a latitude / longitude range box so that the API returns all measurement stations within (see http://aqicn.org/json-api/doc/#api-Map_Queries-GetMapStations). Let's try it out and print the names of the returned stations when searching within the Paris area.

In [14]:
# (latitude, longitude) bottom left, (latitude, longitude) top right
#latlngbox = "48.639956,1.761273,49.159944,2.947797" 
latlngbox="46.342221,6.644529,36.912319,17.894529"
r = requests.get(base_url + f"/map/bounds/?latlng={latlngbox}&token={token}")
[d['station']['name'] for d in r.json()['data']]

['De Amicis, Emilia Romagna, Italy',
 'Borghetto, Pisa, Italy',
 'Staffarda, Revello, Piemonte, Italy',
 'Trbovlje, Slovenia',
 'Novi Travnik Opcina, Bosnia Herzegovina',
 'Ostellato, Emilia Romagna, Italy',
 'Contes, PACA, France',
 'Pavia Folperti, Lombardia, Italy',
 'Dalmine via Verdi, Lombardia, Italy',
 'I.t.i.s. Argine, Napoli, Campania, Italy',
 'Caorle, Emilia Romagna, Italy',
 'Villa Fulvia, Emilia Romagna, Italy',
 'Ajaccio Canetto, France',
 'Brescia Villaggio Sereno, Lombardia, Italy',
 'Milano Senato, Lombardia, Italy',
 'Hum (otok Vis), Croatia',
 'Gherardi, Emilia Romagna, Italy',
 'Isonzo, Emilia Romagna, Italy',
 'Bastia La Marana, France',
 'Ljubljana-Bežigrad, Slovenia',
 'Carducci, Livorno, Italy',
 'Roma, Prato, Italy',
 'Marina-vecchia, Massa, Italy',
 'Saronno Santuario, Lombardia, Italy',
 'Bagno, Cerano, Piemonte, Italy',
 'San Clemente, Emilia Romagna, Italy',
 'Ballirana, Emilia Romagna, Italy',
 'Nova Gorica, Slovenia',
 'Parco Montecucco, Emilia Romagna, I

In [9]:
r.json()

{'status': 'ok',
 'data': {'bounds': '6.749955, 36.619987, 18.480247, 47.115393',
  'parser': 'strconv.ParseFloat: parsing " 36.619987": invalid syntax',
  'reason': 'invalid bounds',
  'status': 'error'}}

# Mapping the data 

The above data is exactly what we need to make a map. To do that, we first turn it into a DataFrame, which is more easy to process.

In [8]:
import pandas as pd

def make_dataframe(r):
    """Extracts data from request r and returns a DataFrame."""
    rows = []
    for item in r.json()['data']:
        rows.append([item['lat'], item['lon'], item['aqi'], item['station']['name']])
    df = pd.DataFrame(rows, columns=['lat', 'lon', 'aqi', 'name'])
    df['aqi'] = pd.to_numeric(df.aqi, errors='coerce')
    return df

df = make_dataframe(r)
df

lat       lon   aqi  \
0   48.827700  2.326700  22.0   
1   48.775900  2.375770  34.0   
2   48.856614  2.352222  41.0   
3   48.930200  2.294210  34.0   
4   48.868600  2.311660  23.0   
5   48.902200  2.390700  12.0   
6   48.840800  2.484400  40.0   
7   48.838600  2.412780  40.0   
8   49.100300  2.343780  31.0   
9   49.063100  1.866400  30.0   
10  48.873300  2.329570  17.0   
11  48.870400  2.332410  17.0   
12  48.902400  2.452610  26.0   
13  49.045900  2.041040  26.0   
14  48.840300  2.634630  14.0   
15  48.850200  2.252580   NaN   
16  48.925100  2.356540  40.0   
17  48.990800  2.444610  33.0   
18  48.891300  2.240640  31.0   
19  48.955700  2.574410  37.0   
20  48.891700  2.345630  17.0   
21  48.830300  2.269720  11.0   
22  48.862100  2.344620  41.0   

                                                name  
0                          Place Victor Basch, Paris  
1                             Vitry-sur-seine, Paris  
2                                              Paris  
3                               Gennevilliers, Paris  
4                   Avenue Des Champs Elysees, Paris  
5                  Route Nationale 2 - Pantin, Paris  
6                            Nogent-sur-marne, Paris  
7                  Boulevard Peripherique Est, Paris  
8   Zone Rurale Nord - Saint-martin-du-tertre, Paris  
9       Zone Rurale Nord-ouest - Fremainville, Paris  
10                        Boulevard Haussmann, Paris  
11                            Place De Lopera, Paris  
12                                    Bobigny, Paris  
13                             Cergy-pontoise, Paris  
14                                     Lognes, Paris  
15             Boulevard Peripherique Auteuil, Paris  
16                 Autoroute A1 - Saint-denis, Paris  
17                                    Gonesse, Paris  
18                                 La Defense, Paris  
19                         Tremblay-en-france, Paris  
20                                Paris 18eme, Paris  
21                        Paris Stade Lenglen, Paris  
22                       Paris 1er Les Halles, Paris

Using this dataframe, we can make an interactive scatter plot using Holoviews:

In [9]:
import holoviews as hv
hv.extension('bokeh', logo=False)

scatter = hv.Scatter(df.dropna(), kdims='lon', vdims=['lat', 'aqi', 'name'])
scatter.opts(color='aqi', size=10, padding=.1, tools=['hover'], colorbar=True, cmap='magma', width=500, height=400, clim=(0, 60))

ImportError: None of the backends could be imported

This is nice, but it would be nicer if could have a background map as well. Fortunately, the Holoviews team has put together a [Geoviews](http://geoviews.org/index.html) package that allows us to do that.

In [10]:
import geoviews as gv
import geoviews.tile_sources as gvts
gv.extension('bokeh', 'matplotlib', logo=False)

points = gv.Points(df.dropna(), ['lon', 'lat'], ['aqi', 'name'])
points.opts(size=10, color='aqi', cmap='magma', tools=['hover'], colorbar=True, width=500, height=400, padding=.1, clim=(0, 60))

gvts.OSM * points  

C:\Anaconda3\lib\site-packages\datashader\transfer_functions.py:21: FutureWarning: xarray subclass Image should explicitly define __slots__
  class Image(xr.DataArray):


:Overlay
   .WMTS.I   :WMTS   [Longitude,Latitude]
   .Points.I :Points   [lon,lat]   (aqi,name)

# An Inverse Distance Weighting map 

The previous plot is nice, since it allows us to visually inspect the data. But it doesnt cover the map. We can do better by using IDW and interpolating the existing points over a grid.

The implementation is copied on https://stackoverflow.com/questions/3104781/inverse-distance-weighted-idw-interpolation-with-python.

In [11]:
import numpy as np

def distance_matrix(x0, y0, x1, y1):
    obs = np.vstack((x0, y0)).T
    interp = np.vstack((x1, y1)).T

    # Make a distance matrix between pairwise observations
    # Note: from <http://stackoverflow.com/questions/1871536>
    # (Yay for ufuncs!)
    d0 = np.subtract.outer(obs[:,0], interp[:,0])
    d1 = np.subtract.outer(obs[:,1], interp[:,1])

    return np.hypot(d0, d1)

def simple_idw(x, y, z, xi, yi):
    dist = distance_matrix(x,y, xi,yi)

    # In IDW, weights are 1 / distance
    weights = 1.0 / dist

    # Make weights sum to one
    weights /= weights.sum(axis=0)

    # Multiply the weights for each interpolated point by all observed Z-values
    zi = np.dot(weights.T, z)
    return zi

To use the above functions, let's now define a grid using meshgrid and interpolate over it.

In [12]:
latlngbox_num = list(map(float, latlngbox.split(',')))

lats = np.linspace(latlngbox_num[0], latlngbox_num[2], num=150)
lons = np.linspace(latlngbox_num[1], latlngbox_num[3], num=151)
meshgrid_shape = (lats.size, lons.size)

xi, yi = np.meshgrid(lons, lats)
xi, yi = xi.ravel(), yi.ravel()

df = df.dropna()
x, y = df.lon.values, df.lat.values
z = df.aqi.values

zi = simple_idw(x, y, z, xi, yi)
zi = zi.reshape(meshgrid_shape)

Let's display the result and compare it to our previous scatter plot.

In [13]:
interpolated = hv.Image(zi[::-1, :])
interpolated.opts(colorbar=True, cmap='magma', tools=['hover'], clim=(0, 60), width=500, height=400)

(scatter + interpolated).cols(1)

:Layout
   .Scatter.I :Scatter   [lon]   (lat,aqi,name)
   .Image.I   :Image   [x,y]   (z)

Finally, let's put this into a geoviews map so that we get a nice background.

In [14]:
import xarray as xr

ds = xr.DataArray(zi, dims=['lat', 'lon'], coords={'lat': lats, 'lon': lons}).to_dataset(name='aqi')

aqi_ds = gv.Dataset(ds, ['lon', 'lat'], 'aqi')

gvts.OSM * gv.Image(aqi_ds).opts(alpha=0.5, width=500, height=400, colorbar=True, clim=(0, 60), cmap='magma')

:Overlay
   .WMTS.I  :WMTS   [Longitude,Latitude]
   .Image.I :Image   [lon,lat]   (aqi)

# Map of Europe

With all these tools in place, we can move on to our final project. Let's make an air quality index map of Europe.

In [15]:
latlngbox = "34.85,-12.7,60.845,30.498"

r = requests.get(base_url + f"/map/bounds/?latlng={latlngbox}&token={token}")

In [16]:
df = make_dataframe(r)

latlngbox_num = list(map(float, latlngbox.split(',')))
lats = np.linspace(latlngbox_num[0], latlngbox_num[2], num=350)
lons = np.linspace(latlngbox_num[1], latlngbox_num[3], num=351)
meshgrid_shape = (lats.size, lons.size)

xi, yi = np.meshgrid(lons, lats)
xi, yi = xi.ravel(), yi.ravel()
df = df.dropna()
x, y = df.lon.values, df.lat.values
z = df.aqi.values

zi = simple_idw(x, y, z, xi, yi)
zi = zi.reshape(meshgrid_shape)

In [17]:
arr = xr.DataArray(zi, dims=['lat', 'lon'], coords={'lat': lats, 'lon': lons}).to_dataset(name='aqi')
aqi_ds = gv.Dataset(arr, ['lon', 'lat'], 'aqi')
aqi_map = gvts.CartoEco * gv.Image(aqi_ds).opts(alpha=0.8, width=500, height=400, colorbar=True, cmap='magma')
aqi_map

:Overlay
   .WMTS.I  :WMTS   [Longitude,Latitude]
   .Image.I :Image   [lon,lat]   (aqi)

Additionaly, we can add a contour plot on top of this.

In [18]:
gvts.CartoEco * aqi_ds.to(gv.FilledContours, ['lon', 'lat']).opts(alpha=0.8, width=500, height=400, 
                                                                  colorbar=True, cmap='magma', levels=10, color_levels=10,
                                                                  tools=['hover'])

:Overlay
   .WMTS.I           :WMTS   [Longitude,Latitude]
   .FilledContours.I :FilledContours   [lon,lat]   (aqi)

# Conclusions 

Judging from the above, it looks like the european air quality is split in two between West and East Europe, with clusters of worse air quality around industrial areas. 
This is a nice finishing point for this analysis, which has taken us from the nicely working WAQI API to some geographical plotting using GeoViews.

*This post was entirely written using the Jupyter Notebook. Its content is BSD-licensed. You can see a static view or download this notebook with the help of nbviewer at [20191126_WorldAirQualityIndexAPI.ipynb](http://nbviewer.ipython.org/urls/raw.github.com/flothesof/posts/master/20191126_WorldAirQualityIndexAPI.ipynb).*